<a href="https://colab.research.google.com/github/PepIngla/PRA1VisualitzacioDades/blob/main/PRA1FinalVisualitzacioDades.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from urllib.request import urlopen
import plotly
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
%pip install chart_studio
import chart_studio.plotly as py
import plotly.express as px
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import json
from google.colab import drive
drive.mount('/content/drive')
home =  'drive/MyDrive/MasterDataScience/VisualitzacioDeDades/'

In [ ]:
# Preparació de les dades
# carrego el mapa de comarques
mapa = open(file=home+'Comarques-Catalunya.txt', mode='rb')#, mode='rb'
mapa_comarques = json.load(mapa)
# carrego el conjunt de dades
df = pd.read_csv(home+'construccioHabitatgePoblacio.csv')
# agrupo per comarca
dfCom = df.groupby(['Any', 'Comarca 2023'#, 'EDAT_n','ESDEVENIMENT_n', 'PAUTA_n'
                    ])['Iniciats anuals','Població'].sum()

#dfCom = dfCom.to_frame()
dfCom['Any'] = dfCom.index.get_level_values(0)
dfCom['Comarca 2023'] = dfCom.index.get_level_values(1)
dfCom = dfCom.reset_index(drop=True)
dfCom = dfCom.sort_values(['Comarca 2023','Any'])
dfCom['Creixement demogràfic'] = dfCom.Població.diff()
dfCom['Canvi de població'] = dfCom.Població.diff() / dfCom.Població
dfCom['Iniciats per 1000 habitants'] = dfCom['Iniciats anuals']*1000 / dfCom.Població
dfCom['Iniciats anuals'] = dfCom['Iniciats anuals'].astype(int)
dfCom['Població'] = dfCom.Població.astype(int)
# El creixement demogràfic a l'any 2000 no està definit
dfCom = dfCom[dfCom['Any']>2000]

# agrupo per àmbit funcional
dfAmbit = df.groupby(['Any', 'Àmbit funcional'])['Iniciats anuals','Població'].sum()

dfAmbit['Any'] = dfAmbit.index.get_level_values(0)
dfAmbit['Àmbit funcional'] = dfAmbit.index.get_level_values(1)
dfAmbit = dfAmbit.reset_index(drop=True)
#Creo dataframes on cada àmbit funcional sigui una columna
columns = dfAmbit['Àmbit funcional'].unique().tolist()
columns.insert(0,'Any')
anys = dfAmbit['Any'].unique().tolist()
dfExpPob=pd.DataFrame(columns=columns)
dfExp=pd.DataFrame(columns=columns)
dfExpPob[columns] = dfExp[columns]
dfExp.Any = anys
dfExpPob.Any = anys
for i, ce in enumerate(columns[1:]):
  mask = dfAmbit['Àmbit funcional'] == ce
  dfExp[ce] = (dfAmbit['Iniciats anuals'][mask]*1e-3).tolist()
  dfExpPob[ce] = (dfAmbit['Població'][mask]*1e-6).tolist()
dfExp['total'] = dfExp[columns[1:]].sum(axis=1)
dfExpPob['total'] = dfExpPob[columns[1:]].sum(axis=1)


In [5]:
##### Stream graphs:
colors = ['#636EFA', '#EF553B', '#00CC96', '#AB63FA',
          '#FFA15A', '#19D3F3', '#FF6692', '#B6E880',
          '#FF97FF', '#FECB52']
fig = make_subplots(rows=1, cols=2)
yacc =  -dfExp['total'] / 2
yacc2 =  -dfExpPob['total'] / 2
fig.append_trace(go.Scatter(name='baseline', x=dfExp['Any'], y = yacc,
                          line = dict(color='rgba(0,0,0,0)'),
                          hoverinfo='skip',showlegend=False),row=1, col=1)

fig.append_trace(go.Scatter(name='baseline', x=dfExp['Any'], y = yacc2,
                          line = dict(color='rgba(0,0,0,0)'),
                          hoverinfo='skip',showlegend=False),row=1, col=2)
for i, col in enumerate(columns[1:]):
  yacc += dfExp[col]
  fig.append_trace(go.Scatter(name=col, x=dfExp['Any'], y = yacc,
                            line = dict(color='rgba(0,0,0,0)'),
                            fill='tonexty', fillcolor=colors[i],
                            text=((dfExp[col]*1e3).astype(int)*1e-3).astype(str)+"milers d'habitatges",
                            hoverinfo='name+text',showlegend=False),row=1, col=1)#,

  yacc2 += dfExpPob[col]
  fig.append_trace(go.Scatter(name=col, x=dfExpPob['Any'], y = yacc2,
                            line = dict(color='rgba(0,0,0,0)'),
                            fill='tonexty', fillcolor=colors[i],
                            text=(dfExpPob[col]*1e3).astype(int).astype(str)+" milers d'habitants",
                            hoverinfo='name+text',showlegend=False),row=1, col=2)


buttons = []
ylist = [0.0, 0.05, 0.11,0.17, 0.5, 0.9, 0.95,1]
for i, curve in enumerate(columns[1:]):
    visible = [False]*len(columns[1:])
    visible[i] = True  # Only the selected curve will be visible
    buttons.append(dict(label=curve, method='update', args=[{'visible': visible}]))
    itrans = 4
    if i<4:
      y = 0.2+0.06*i
    else:
      y = 0.6+0.06*(i-4)
    fig.add_annotation( x=0.2, y=y, xanchor='left', yanchor='middle', align='left', xref='paper', yref='paper',
    text=curve, showarrow=False, font=dict(color=colors[i],size=16))

fig.add_annotation(
    text='Habitatges construïts per àmbit funcional', xref='paper', yref='paper', x=0.25, y=1.1,
    showarrow=False, font=dict(size=20), xanchor='center', align='center', textangle=0)#, color='white'

fig.add_annotation(
    text='Població per àmbit funcional', xref='paper', yref='paper', xanchor='center', x=0.75, y=1.1,
    showarrow=False, font=dict(size=20), align='center', textangle=0) #, color='white'
fig.update_layout(width=1000,height=470,
                  plot_bgcolor='rgba(0,0,0,0)',
                  margin=dict(l=20, r=20, b=50, t=120, pad=10))

fig.add_annotation(
    text='Una visió global:', xref='paper', yref='paper', x=0.5, y=1.4,
    showarrow=False, font=dict(size=25), xanchor='center', align='center', textangle=0)#, color='white'
fig.add_annotation(
    text='<i> Construcció indiscriminada i creixement demogràfic 2000-2008</i>', xref='paper', yref='paper', x=0.5, y=1.25,
    showarrow=False, font=dict(size=20), xanchor='center', align='center', textangle=0)#, color='white'
# Remove the grid
fig.update_xaxes(showgrid=False)
fig.update_yaxes(showgrid=False)

fig['layout']['xaxis'].update(title_text='Any')
fig['layout']['xaxis2'].update(title_text='Any')

fig['layout']['yaxis'].update(title_text='Habitatges construïts (milers)')
fig['layout']['yaxis2'].update(title_text="Població (milions d'habitants)")
fig.write_html(home+'flowcharts.html')
f=open(home+'Output_graph.html', 'w')
f.write(fig.to_html(full_html=False, include_plotlyjs='cdn'))
f.close()
fig.show()
#### Coropletes
fig = make_subplots(rows=1, cols=2,
                    specs=[[{"type": "choropleth"},{"type": "choropleth"}],],
                           horizontal_spacing = 0.0,)
min_ini = np.min(dfCom['Iniciats per 1000 habitants'])
max_ini = np.max(dfCom['Iniciats per 1000 habitants'])
if dfCom['Creixement demogràfic'].apply(type)[46] != str:
  dfCom['Creixement demogràfic']=dfCom['Creixement demogràfic'].astype(int).astype(str) + ' habitants'
max_pob = np.max(dfCom['Canvi de població'])
# Add traces, one for each slider step
for year in dfCom.Any.unique():
    filtered_df = dfCom[dfCom.Any == year]

    fig.append_trace(go.Choropleth(
                         featureidkey="properties.nom_comar",
                         geojson=mapa_comarques,
                         locations=filtered_df['Comarca 2023'],
                         z=filtered_df['Iniciats per 1000 habitants'],#

                         zmin=min_ini, zmax=max_ini,
                         colorscale="inferno",
                         colorbar_title='',#Habitatges construïts per 1000 habitants
                         showscale= True,
                         text=filtered_df['Iniciats anuals'].astype(str) +' habitatges<br>'+
                         filtered_df['Iniciats per 1000 habitants'].round(decimals=1).astype(str)+' habitatges per 1000 habitants',
                         hoverinfo='location+text'), row=1, col=1)

    fig.append_trace(go.Choropleth(
                         featureidkey="properties.nom_comar",
                         geojson=mapa_comarques,
                         locations=filtered_df['Comarca 2023'],
                         z=filtered_df['Canvi de població'],
                         zmin=-max_pob, zmax=max_pob,
                         colorscale='RdBu',#"rdylgn",

                         showscale= True,
                         text=(filtered_df['Canvi de població']*100).round(decimals=1).astype(str)+'%<br>'+filtered_df['Creixement demogràfic'],
                         colorbar=dict(title='',
                                       tickformat='.0%'),
                         hoverinfo='location+text'), row=1, col=2)


#fig.data[1].visible = True


# Create and add slider
steps = []
for i in range(int(len(fig.data)/2)):
    step = dict(method="restyle",
        args=["visible", [False] * len(fig.data)],
                label=str(dfCom.Any.unique()[i]) #int(i/2)
    )
    #step["args"][1][i] = True
    #step["args"][1][i+1] = True # This shows them both but still not correct(Showing wrong traces 1,2)
    step["args"][1][2*i:2*i+2] = [True, True]
    steps.append(step)

sliders = [dict(
    active=0,
    currentvalue={"prefix": "Any:  "},
    pad={"t": 50},
    steps=steps,
    len=0.5, x=0.5, xanchor='center',
    y=0.0, yanchor='middle'

)]
fig.update_geos(visible=False, fitbounds="locations") # tapo el mapa per defecte que no es gaire acurat
ind_left=[2*i for i in range(int(len(fig.data)/2))]
for i in range(len(fig.data)):
  fig.data[i].colorbar.x=0.905
  fig.data[i].colorbar.thickness=10
  fig.data[i].colorbar.len=0.5
  #.update_layout(coloraxis=dict(showscale=False)
for i in ind_left:
  fig.data[i].colorbar.x = 0.405 # Set the x position of the colorbar
#fig.update_yaxes(title_text="Temperature", range=[-160, 260],nticks=30, row=1, col=1)
#fig.update_yaxes(title_text="Pressure", range=[-169, 260],nticks=30, row=2, col=1)
#sliders=sliders,
fig.update_layout(sliders=sliders, width=1000,height=560, # template ="plotly_dark",
                  margin=dict(l=20, r=0, b=150, t=110, pad=10))
last_frame_num = int(len(fig.data)/2) - 1
fig.layout['sliders'][0]['active'] = last_frame_num
coltext = 'black'
fig.add_annotation(
    text='Creixement demogràfic relatiu', xref='paper', yref='paper', x=0.98, y=0.5,
    showarrow=False, font=dict(size=15, color=coltext), align='center', textangle=-90)
fig.add_annotation(
    text='Creixement demogràfic', xref='paper', yref='paper', x=0.75, y=1.1,xanchor='center',
    showarrow=False, font=dict(size=20, color=coltext), align='center', textangle=0)
fig.add_annotation(
    text='Construïts per 1000 habitants', xref='paper', yref='paper', x=0.47, y=0.5,
    showarrow=False, font=dict(size=15, color=coltext), align='center', textangle=-90)
fig.add_annotation(
    text='Habitatges construïts', xref='paper', yref='paper', x=0.25, y=1.1,xanchor='center',
    showarrow=False, font=dict(size=20, color=coltext), align='center', textangle=0)#, color='white'
fig.add_annotation(
    text='Una visió comarcal:', xref='paper', yref='paper', x=0.5, y=1.4,
    showarrow=False, font=dict(size=25), xanchor='center', align='center', textangle=0)#, color='white'
fig.add_annotation(
    text='<i>Retorn al camp post-covid</i>', xref='paper', yref='paper', x=0.5, y=1.25,
    showarrow=False, font=dict(size=20), xanchor='center', align='center', textangle=0)#, color='white'
fig.add_annotation(
    text='Dades obertes Generalitat de Catalunya: <a href="https://analisi.transparenciacatalunya.cat/Habitatge/Habitatges-iniciats-i-acabats-S-rie-hist-rica-trim/j8h8-vxug">'+
    'Habitatges construïts</a> i <a href="https://analisi.transparenciacatalunya.cat/Sector-P-blic/Dades-hist-riques-de-poblaci-dels-municipis-de-Cat/x5sz-niat">població</a> per municipi',
    xref='paper', yref='paper', x=0.5, y=-0.35,
    showarrow=False, font=dict(size=15), xanchor='center', align='right', textangle=0)#, color='white'
fig.add_annotation(
    text='Mapa de comarques: <a href="https://github.com/aariste/GeoJSON-Mapas"> aariste </a>',
    xref='paper', yref='paper', x=0.5, y=-0.45,
    showarrow=False, font=dict(size=15), xanchor='center', align='right', textangle=0)#, color='white'
fig.write_html(home+'coropletes_sincronitzades.html')
f=open(home+'Output_graph.html', 'a')
f.write(fig.to_html(full_html=False, include_plotlyjs='cdn'))
f.close()
fig.show()